In [1]:
import numpy as np
from pathlib import Path
from scripts.planar_pushing.create_plan import get_sugar_box
from planning_through_contact.geometry.planar.planar_pose import PlanarPose
from planning_through_contact.planning.planar.planar_plan_config import (
    PlanarPlanConfig,
    PlanarSolverParams,
    SliderPusherSystemConfig,
)
from planning_through_contact.planning.planar.planar_pushing_planner import (
    PlanarPushingPlanner,
)
from planning_through_contact.visualize.planar import (
    visualize_planar_pushing_trajectory,
)
from IPython.display import HTML, SVG, display
import pydot

In [2]:
slider = get_sugar_box()
pusher_radius = 0.035

dynamics_config = SliderPusherSystemConfig(pusher_radius=pusher_radius, slider=slider)

config = PlanarPlanConfig(
    time_non_collision=2.0,
    time_in_contact=2.0,
    num_knot_points_contact=4,
    num_knot_points_non_collision=4,
    avoid_object=True,
    avoidance_cost="quadratic",
    no_cycles=False,
    dynamics_config=dynamics_config,
    allow_teleportation=False,
    use_redundant_dynamic_constraints=True,
)

planner = PlanarPushingPlanner(config)

solver_params = PlanarSolverParams(
    gcs_max_rounded_paths=10,
    print_flows=False,
    assert_determinants=True,
    print_solver_output=False,
    print_path=True,
    measure_solve_time=True,
    nonlinear_traj_rounding=False,
)


In [3]:
def plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose, rounded_and_original: bool = False):
    planner.set_initial_poses(finger_initial_pose, slider_initial_pose)
    planner.set_target_poses(finger_target_pose, slider_target_pose)

    if rounded_and_original:
        traj_original, traj_rounded = planner.plan_trajectory(solver_params)
        return (
            HTML(
                visualize_planar_pushing_trajectory(
                    traj_original, visualize_knot_points=True
                ).to_jshtml()
            ),
            HTML(
                visualize_planar_pushing_trajectory(
                    traj_rounded, visualize_knot_points=True
                ).to_jshtml()
            )
        )
    else:
        traj_original = planner.plan_trajectory(solver_params)
        return HTML(
                visualize_planar_pushing_trajectory(
                    traj_original, visualize_knot_points=True
                ).to_jshtml()
            )

import base64

def svg_to_fixed_width_html_image(svg, width="70%"):
    b64 = base64.b64encode(svg).decode("utf=8")
    text = f'<img width="{width}" src="data:image/svg+xml;base64,{b64}" >'
    return HTML(text)

def show_gcs_diagram(gcs):
    graphviz = gcs.GetGraphvizString()
    data = pydot.graph_from_dot_data(graphviz)[0]
    display(svg_to_fixed_width_html_image(data.create_svg()))


In [4]:
show_gcs_diagram(planner.gcs)

#### Some adverserial examples

1. Pushing down from above

In [5]:
slider_initial_pose = PlanarPose(x=0.0, y=0.0, theta=0.0)
slider_target_pose = PlanarPose(x=0.0, y=-0.3, theta=0.0)
finger_initial_pose = PlanarPose(x=0.0, y=0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

INFO:drake:Solved GCS shortest path using Mosek with convex_relaxation=true and preprocessing=true and rounding.
INFO:drake:Finished 100 rounding trials.


Total elapsed optimization time: 61.58700180053711
path: ['source', 'ENTRY_NON_COLL_0', 'FACE_0', 'EXIT_NON_COLL_0', 'target']


2. Pushing down from below

In [6]:
slider_initial_pose = PlanarPose(x=0.0, y=0.0, theta=0.0)
slider_target_pose = PlanarPose(x=0.0, y=-0.3, theta=0.0)
finger_initial_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

INFO:drake:Solved GCS shortest path using Mosek with convex_relaxation=true and preprocessing=true and rounding.


Source vertex is already set, removing old vertex and adding new
Target vertex is already set, removing old vertex and adding new


AssertionError: 

3. The same, but translated 

In [ ]:
OFFSET = 0.5
slider_initial_pose = PlanarPose(x=0.0+OFFSET, y=0.0+OFFSET, theta=0.0)
slider_target_pose = PlanarPose(x=0.0+OFFSET, y=-0.3+OFFSET, theta=0.0)
finger_initial_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

4. The same, but rotated

In [ ]:
TH_OFFSET = 0.5
R = np.array([[np.cos(TH_OFFSET), -np.sin(TH_OFFSET)], [np.sin(TH_OFFSET), np.cos(TH_OFFSET)]])
pos_initial = R.dot(slider_initial_pose.pos)
pos_target = R.dot(slider_target_pose.pos)

slider_initial_pose = PlanarPose(pos_initial[0,0], pos_initial[1,0], 0)
slider_target_pose = PlanarPose(pos_target[0,0], pos_target[1,0], 0)
finger_initial_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

In [ ]:
TH_OFFSET = -0.5
R = np.array([[np.cos(TH_OFFSET), -np.sin(TH_OFFSET)], [np.sin(TH_OFFSET), np.cos(TH_OFFSET)]])
pos_initial = R.dot(slider_initial_pose.pos)
pos_target = R.dot(slider_target_pose.pos)

slider_initial_pose = PlanarPose(pos_initial[0,0], pos_initial[1,0], 0)
slider_target_pose = PlanarPose(pos_target[0,0], pos_target[1,0], 0)
finger_initial_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

Rotated by pi

In [ ]:
TH_OFFSET = np.pi/2
R = np.array([[np.cos(TH_OFFSET), -np.sin(TH_OFFSET)], [np.sin(TH_OFFSET), np.cos(TH_OFFSET)]])
pos_initial = R.dot(slider_initial_pose.pos)
pos_target = R.dot(slider_target_pose.pos)

slider_initial_pose = PlanarPose(pos_initial[0,0], pos_initial[1,0], 0)
slider_target_pose = PlanarPose(pos_target[0,0], pos_target[1,0], 0)
finger_initial_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

In [ ]:
TH_OFFSET = np.pi
R = np.array([[np.cos(TH_OFFSET), -np.sin(TH_OFFSET)], [np.sin(TH_OFFSET), np.cos(TH_OFFSET)]])
pos_initial = R.dot(slider_initial_pose.pos)
pos_target = R.dot(slider_target_pose.pos)

slider_initial_pose = PlanarPose(pos_initial[0,0], pos_initial[1,0], 0)
slider_target_pose = PlanarPose(pos_target[0,0], pos_target[1,0], 0)
finger_initial_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

In [ ]:
TH_OFFSET = (3/2) * np.pi
R = np.array([[np.cos(TH_OFFSET), -np.sin(TH_OFFSET)], [np.sin(TH_OFFSET), np.cos(TH_OFFSET)]])
pos_initial = R.dot(slider_initial_pose.pos)
pos_target = R.dot(slider_target_pose.pos)

slider_initial_pose = PlanarPose(pos_initial[0,0], pos_initial[1,0], 0)
slider_target_pose = PlanarPose(pos_target[0,0], pos_target[1,0], 0)
finger_initial_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=-0.2, theta=0.0)

original = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)

----

Test a few different trajectories:

In [ ]:
slider_initial_pose = PlanarPose(x=0.55, y=0.0, theta=0.0)
slider_target_pose = PlanarPose(x=0.65, y=0.0, theta=-0.5)
finger_initial_pose = PlanarPose(x=-0.2, y=-0.2, theta=0.0)
finger_target_pose = PlanarPose(x=-0.2, y=-0.2, theta=0.0)

original, rounded = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)
display(rounded)

The next one is infeasible...

In [ ]:
slider_initial_pose = PlanarPose(x=0.60, y=0.1, theta=-0.2)
slider_target_pose = PlanarPose(x=0.70, y=-0.2, theta=0.5)
finger_initial_pose = PlanarPose(x=-0.2, y=0.0, theta=0.0)
finger_target_pose = PlanarPose(x=-0.2, y=0.0, theta=0.0)

original, rounded = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)
display(rounded)

In [ ]:
slider_initial_pose = PlanarPose(x=0.60, y=0.1, theta=np.pi / 2)
slider_target_pose = PlanarPose(x=0.70, y=-0.05, theta=np.pi / 2 + 0.4)
finger_initial_pose = PlanarPose(x=-0.2, y=0.0, theta=0.0)
finger_target_pose = PlanarPose(x=0.0, y=0.2, theta=0.0)

original, rounded = plan_and_visualize(slider_initial_pose, slider_target_pose, finger_initial_pose, finger_target_pose)
display(original)
display(rounded)